## Imperial Valley Subsidence, CA USA (2015)

The InSAR.dev ecosystem, the PyGMTSAR InSAR library, the Geomed3D geophysical inversion library, and N-Cube 3D/4D GIS data visualization (among others) are open-source projects I develop in my free time.

I hold a Master’s degree in STEM, specializing in radio physics. In 2004, I received first prize in the All-Russian Physics Competition for significant results in forward and inverse modeling for nonlinear optics and holography. These skills are also applicable to modeling gravity, magnetic, and thermal fields, as well as satellite interferometry processing.

With 20 years of experience as a data scientist and software developer, I have contributed to scientific and industrial development through government contracts, university projects, and work with companies including LG Corp and Google Inc.

You can support my work on Patreon, where I share updates on my projects, publications, use cases, examples, and other useful information. For research and development services and support, please visit my profile on the freelance platform Upwork.

You can support my work on [Patreon](https://www.patreon.com/pechnikov), where I share updates on my projects, publications, use cases, examples, and other useful information. For research and development services and support, please visit my profile on the freelance platform [Upwork](https://www.upwork.com) or reach out to me directly.

### Resources
- Google Colab Pro notebooks and articles on [Patreon](https://www.patreon.com/pechnikov),
- Google Colab notebooks on [GitHub](https://github.com),
- Docker Images on [DockerHub](https://hub.docker.com),
- Geological Models on [YouTube](https://www.youtube.com),
- VR/AR Geological Models on [GitHub](https://github.com),
- Live updates and announcements on [LinkedIn](https://www.linkedin.com/in/alexey-pechnikov/).

© Alexey Pechnikov, 2025

$\large\color{blue}{\text{Hint: Use menu Cell} \to \text{Run All or Runtime} \to \text{Complete All or Runtime} \to \text{Run All}}$
$\large\color{blue}{\text{(depending of your localization settings) to execute the entire notebook}}$

# Stage 1. InSAR.dev-PyGMTSAR: A Python package for InSAR pre-processing with PyGMTSAR

Convert Sentinel-1 SLC data using GMTSAR binaries into a geocoded, cloud-ready Zarr dataset on Google Colab or in a Docker container. The output can be hosted on GitHub or any file storage as a set of files or a single ZIP archive.

For Stage 2 InSAR analysis, only a pure-Python package is required—no binary installation needed—so processing can run on any Windows, macOS, or Linux host.

## Google Colab Installation

Install InSAR.dev Python libraries and required GMTSAR binaries

In [ ]:
import sys
if 'google.colab' in sys.modules:
    # install the exact commit (no pip cache)
    !{sys.executable} -m pip install --no-cache-dir \
      "git+https://github.com/AlexeyPechnikov/InSARdev.git#subdirectory=insardev_toolkit"
    !{sys.executable} -m pip install --no-cache-dir \
      "git+https://github.com/AlexeyPechnikov/InSARdev.git#subdirectory=insardev_pygmtsar"
    !{sys.executable} -m pip install --no-cache-dir \
      "git+https://github.com/AlexeyPechnikov/InSARdev.git#subdirectory=insardev"

In [ ]:
import platform, sys, os
if 'google.colab' in sys.modules:
    # script URL: https://github.com/AlexeyPechnikov/InSARdev/blob/main/insardev_pygmtsar/insardev_pygmtsar/data/google_colab.sh
    import importlib.resources as resources
    with resources.as_file(resources.files('insardev_pygmtsar.data') / 'google_colab.sh') as google_colab_script_filename:
        !sh {google_colab_script_filename}
    from google.colab import output
    output.enable_custom_widget_manager()

# specify GMTSAR installation path
PATH = os.environ['PATH']
if PATH.find('GMTSAR') == -1:
    PATH = os.environ['PATH'] + ':/usr/local/GMTSAR/bin/'
    %env PATH {PATH}

## Import Python Modules

In [ ]:
import numpy as np
import geopandas as gpd
import shapely
import json
import matplotlib.pyplot as plt
%matplotlib inline
# setup dark theme
from insardev.UI import UI
UI('dark')

In [ ]:
# print versions
from insardev_pygmtsar import __version__ as pygmtsar_version
from insardev_toolkit import __version__ as toolkit_version
print("insardev_pygmtsar version:", pygmtsar_version)
print("insardev_toolkit version:", toolkit_version)
# import modules to be used in the notebook
from insardev_pygmtsar import S1
from insardev_toolkit import EOF, ASF, Tiles, XYZTiles

## Specify Sentinel-1 SLC Bursts and Area

### Descending Orbit Bursts

https://search.asf.alaska.edu/#/?polygon=LINESTRING(-115.3%2032.1,-115.1%2032.6)&searchType=Geographic%20Search&searchList=S1A_IW_SLC__1SSV_20150121T134412_20150121T134426_004270_005317_DBBE&resultsLoaded=true&granule=S1_370325_IW1_20150121T134413_VV_DBBE-BURST&zoom=8.486&center=-115.992,31.568&dataset=SENTINEL-1%20BURSTS&start=2015-01-20T17:00:00Z&end=2015-05-21T16:59:59Z&flightDirs=Descending&path=173-173

In [ ]:
# Specify bursts to download
BURSTS = """
S1_370328_IW1_20150521T134424_VV_13DD-BURST
S1_370327_IW1_20150521T134421_VV_13DD-BURST
S1_370326_IW1_20150521T134418_VV_13DD-BURST
S1_370325_IW1_20150521T134415_VV_13DD-BURST
S1_370328_IW1_20150427T134423_VV_C1D8-BURST
S1_370327_IW1_20150427T134420_VV_C1D8-BURST
S1_370326_IW1_20150427T134417_VV_C1D8-BURST
S1_370325_IW1_20150427T134414_VV_C1D8-BURST
S1_370328_IW1_20150403T134421_VV_3A7A-BURST
S1_370327_IW1_20150403T134419_VV_3A7A-BURST
S1_370326_IW1_20150403T134416_VV_3A7A-BURST
S1_370325_IW1_20150403T134413_VV_3A7A-BURST
S1_370328_IW1_20150310T134421_VV_36B8-BURST
S1_370327_IW1_20150310T134418_VV_36B8-BURST
S1_370326_IW1_20150310T134415_VV_36B8-BURST
S1_370325_IW1_20150310T134412_VV_36B8-BURST
S1_370328_IW1_20150121T134421_VV_DBBE-BURST
S1_370327_IW1_20150121T134418_VV_DBBE-BURST
S1_370326_IW1_20150121T134415_VV_DBBE-BURST
S1_370325_IW1_20150121T134413_VV_DBBE-BURST
"""
BURSTS = list(filter(None, BURSTS.split('\n')))
print (f'Bursts defined: {len(BURSTS)}')

## Specify Directories

In [ ]:
# directory where Sentinel-1 bursts and orbits will be downloaded
DATADIR = 'data'
# path to the downloaded DEM file
DEM = f'{DATADIR}/dem.nc'
ZARRDIR = 'zarr'

## Download and Unpack Datasets

### Enter Your ASF User and Password

If the data directory is empty or doesn't exist, you'll need to download Sentinel-1 scenes from the Alaska Satellite Facility (ASF) datastore. Use your Earthdata Login credentials. If you don't have an Earthdata Login, you can create one at https://urs.earthdata.nasa.gov//users/new

You can also use pre-existing SLC scenes stored on your Google Drive, or you can copy them using a direct public link from iCloud Drive.

The credentials below are available at the time the notebook is validated.

In [ ]:
# Set these variables to None and you will be prompted to enter your username and password below.
asf_username = 'GoogleColab2023'
asf_password = 'GoogleColab_2023'

In [ ]:
# Set these variables to None and you will be prompted to enter your username and password below.
asf = ASF(asf_username, asf_password)
print(asf.download(DATADIR, BURSTS))

In [ ]:
# read the notices printed below carefully
s1 = S1(DATADIR)
s1.to_dataframe().to_file(f"{DATADIR}/s1.geojson", driver="GeoJSON")
#df = gpd.read_file("s1.geojson")
s1.to_dataframe()

In [ ]:
# scan the data directory for Sentinel-1 SLC bursts and download related orbits
EOF().download(DATADIR, s1.to_dataframe())

In [ ]:
s1.to_dataframe()

In [ ]:
# download Copernicus Global DEM 1 arc-second
Tiles().download_dem(s1.to_dataframe(), provider='GLO', filename=DEM)[::4,::4].plot.imshow(cmap='cividis')

## Preprocess Sentinel-1 SLC to Geocoded Zarr

In [ ]:
# scan SLC bursts with DEM
s1 = S1(DATADIR, DEM=DEM)
s1.to_dataframe()

In [ ]:
# descending orbit bursts: preview
s1.plot(ref='2015-01-21')

In [ ]:
# descending orbit bursts: load SLC bursts with DEM and transform to ZARR
# use lower resolution for Google Colab, default is (20, 5)
# the /tmp directory is extremely slow on Google Colab; use a RAM disk for temporary files
s1.transform(ZARRDIR, ref='2015-01-21',
             n_jobs=os.cpu_count() // 2 if 'google.colab' in sys.modules else None,
             tmpdir='/dev/shm' if 'google.colab' in sys.modules else None)

# Stage 2. InSAR.dev: A Pure-Python package for InSAR processing

For InSAR analysis, only a pure-Python package is required—no binary installation needed—so processing can run on any Windows, macOS, or Linux host.

## Import Python Modules

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
# setup dark theme
from insardev.UI import UI
UI('dark')

In [ ]:
import sys
if 'google.colab' in sys.modules:
    !{sys.executable} -m pip install --no-cache-dir \
        "git+https://github.com/AlexeyPechnikov/InSARdev.git#subdirectory=insardev"

In [ ]:
# print versions
from insardev import __version__ as insardev_version
from insardev_toolkit import __version__ as toolkit_version
print("insardev version:", insardev_version)
print("insardev_toolkit version:", toolkit_version)
# import modules to be used in the notebook
from insardev import Stack, BatchUnit
# data downloader
from insardev_toolkit.HTTP import unzip

In [ ]:
# common data science libraries
import xarray as xr
import numpy as np
import rioxarray as rio

In [ ]:
# 3D plotting modules
import pyvista as pv
# white background
#pv.set_plot_theme("document")
pv.set_plot_theme("dark")
from IPython.display import display, HTML
if 'google.colab' in sys.modules:
    import panel
    panel.extension(comms='ipywidgets')
    panel.extension('vtk')
# 2D interactive map modules
import json
import matplotlib.colors
from ipyleaflet import Map, GeoJSON, LayersControl, basemaps, basemap_to_tiles

## Specify Directories

In [ ]:
ZARRDIR = 'zarr'
WORKDIR = 'workdir'

## Download and Unpack Datasets

We can process datasets hosted on GitHub, Zenodo, or other platforms in a single workflow.

In [ ]:
# example downloading command
#unzip("https://zenodo.org/records/15347694/files/Türkiye_Elevation-40x10-004.zip", ZARRDIR)

## Run Local Dask Cluster

Launch a Dask cluster for local or distributed multicore computing. This makes it possible to process terabyte-scale Sentinel-1 SLC datasets even on an Apple MacBook Air with 16 GB of RAM.

In [ ]:
# simple Dask initialization
if 'client' in globals():
    client.shutdown()
from dask.distributed import Client
client = Client(silence_logs='CRITICAL', threads_per_worker=2)
client

## Load Geocoded Bursts

In [ ]:
stack = Stack().load(ZARRDIR).align_elevation()
stack

In [ ]:
stack.plot(cmap='autumn', alpha=0.15)
# download the basemap adding the buffer to cover the area of interest after reprojecting
gmap = XYZTiles().download_googlesatellite(stack.to_dataframe().buffer(5_000), zoom=10, fill_value=0)
gmap.plot.imshow(ax=plt.gca(), zorder=-1, add_labels=False)
plt.gca().set_title(f'Sentinel-1 Burst Footprints');

## Compute Baseline

In [ ]:
baseline = stack.baseline(days=100, meters=150)
baseline

In [ ]:
baseline.plot();

In [ ]:
baseline.hist();

## Compute Interferograms

In [ ]:
# lazy calculation
intf, corr = stack.phasediff_multilook(baseline.tolist(), wavelength=100, goldstein=32)
intf

In [ ]:
# downsample and materialize interferogram and correlation
intf, corr = stack.compute(intf.downsample(30), corr.downsample(30))

In [ ]:
# align and unify bursts
intf = intf.align().dissolve().compute()
corr = corr.dissolve().compute()

In [ ]:
intf.plot(rows=3, cols=3, size=2.5);

In [ ]:
corr.plot(rows=3, cols=3, size=2.5);

In [ ]:
stack.to_vtk('intf', intf.downsample(100))

In [ ]:
# build interactive 3D plot
plotter = pv.Plotter(notebook=True)
mesh = pv.read('intf/VV.vtk').scale([1, 1, 4], inplace=True)
plotter.add_mesh(mesh, scalars='20150121_20150427', cmap='turbo', ambient=0.1, show_scalar_bar=True)
plotter.show_axes()
bounds = mesh.bounds
center = mesh.center
# move camera closer by reducing distance (zoom in)
distance = mesh.length / 1.4
plotter.camera.position = (center[0] + distance, center[1] + distance, center[2] + distance * 0.5)
plotter.camera.focal_point = center
plotter.camera.azimuth = 215
plotter.camera.elevation = 15
plot = plotter.show(screenshot='3D Interferogram.png', jupyter_backend='panel' if 'google.colab' in sys.modules else 'client', return_viewer=True)
if 'google.colab' in sys.modules:
    plot = panel.panel(
        plotter.render_window, orientation_widget=plotter.renderer.axes_enabled,
        enable_keybindings=False, sizing_mode='stretch_width', min_height=600
    )
display(HTML('<h1 style="text-align:center; margin-bottom:0;">Interactive Sentinel-1 Interferogram on DEM</h1>'))
plot

## Unwrap Interferograms

In [ ]:
# unwrap as a single raster on auto-detected GPU or fallback to CPU
phase2d = stack.unwrap2d_dataset(intf.to_dataset(), corr.to_dataset(), device='auto')
phase2d

In [ ]:
# convert back to burst stack and materialize
phase = intf.from_dataset(phase2d).compute()

In [ ]:
phase.plot(rows=3, cols=3, size=2.5, quantile=[0.01, 0.99], alpha=0.8);

## Detrend Unwrapped Phase

In [ ]:
phase_detrend = phase - phase.gaussian(wavelength=40000).compute()

In [ ]:
phase_detrend.plot(rows=3, cols=3, size=2.5, quantile=[0.01, 0.99], alpha=0.8)

## Convert Phase to Line-of-Sight (LOS) Displacement

In [ ]:
displacement = stack.displacement_los(phase_detrend).compute()
displacement

## Compute Accumulated Displacement Time Series

In [ ]:
displacement_cum = stack.lstsq(displacement, corr).compute()
displacement_cum

In [ ]:
displacement_cum.isel(date=slice(1,None)).plot(quantile=[0.001, 0.999], alpha=0.8)

In [ ]:
displacement_cum.isel(date=slice(1,None)).sel(y=slice(3_580_000, 3_593_000), x=slice(665_000, 678_000)).plot(quantile=[0.001, 0.999], alpha=0.8)

## Plot Pixel Displacement Time Series

In [ ]:
# define point coordinates (as in the PyGMTSAR notebook): lat = 32.43, lon = -115.15
y = 3_589_600
x = 674_000

# find nearest pixel to the defined coordinates
displacement_pixel = displacement_cum.to_dataset().VV.sel(y=y, x=x, method='nearest').fillna(0)
displacement_pixel

In [ ]:
(1000*displacement_pixel).plot.scatter('date')
(1000*displacement_pixel).plot(lw=0.5, color='w')
plt.title(f'Cumulative LOS Displacement\ny={y}, x={x}', fontsize=18)
plt.xlabel('Date', fontsize=14)
plt.ylabel('Displacement, [mm]', fontsize=16)
plt.grid()
plt.savefig('Cumulative LOS Displacement POI, [mm].jpg')

## 2D Interactive Map

The map is also available as a standalone web page, which can be saved and used locally or shared on any web platform: https://insar.dev/ui/Imperial_Valley_2015.html

In [ ]:
velocity = displacement_cum.velocity().compute()

In [ ]:
# convert velocity in mm/year to GeoJSON for mapping on ipyleaflet
geojson = (1000*velocity).sel(y=slice(3_570_000, 3_600_000), x=slice(655_000, 685_000)).downsample(500).to_geojson(crs='EPSG:4326')

In [ ]:
# Parse the string FIRST
geojson = json.loads(geojson)

# Create a colormap for velocities
colormap = plt.get_cmap('turbo')
def velocity_to_color(velocity, limits=[-60, 60]):
    normalized = np.clip((velocity - limits[0]) / (limits[1] - limits[0]), 0, 1)
    return matplotlib.colors.to_hex(colormap(normalized))

# Embed styles directly into GeoJSON properties
for feature in geojson['features']:
    color = velocity_to_color(feature['properties']['VV'])
    feature['properties']['style'] = {
        'color': color,
        'weight': 1,
        'fillColor': color,
        'fillOpacity': 0.4
    }

# Initialize the map with Esri Satellite as default
location = [32.40318, -115.18128]
osm_layer = basemap_to_tiles(basemaps.OpenStreetMap.Mapnik)
osm_layer.base = True
osm_layer.name = 'OpenStreetMap'
esri_base = basemap_to_tiles(basemaps.Esri.WorldImagery)
esri_base.base = True
esri_base.name = 'Esri Satellite'
m = Map(center=location, zoom=12, layers=[osm_layer, esri_base], scroll_wheel_zoom=True, layout=dict(height='620px'))

# Add GeoJSON layer - already a dict now
geo_json = GeoJSON(
    data=geojson,
    style_callback=lambda feature: feature['properties']['style'],
    hover_style={'fillOpacity': 1},
    name='InSAR'
)
m.add_layer(geo_json)

m.add_control(LayersControl(position='topright'))
display(m)

## Save the Results

Save the results in geospatial data formats like to NetCDF, GeoTIFF and others. The both formats (NetCDF and GeoTIFF) can be opened in QGIS and other GIS applications.

In [ ]:
# save the accumulated displacement in mm as a GeoTIFF file
(1000*displacement_cum).to_dataset().VV[-1].rio.to_raster('displacement.tif')

In [ ]:
# save the interactive map as an HMTL file
m.save('Imperial_Valley_2015_ipyleaflet.html', title='InSAR Velocity Map')

## Export from Google Colab

In [ ]:
if 'google.colab' in sys.modules:
    from google.colab import files
    files.download('Imperial_Valley_2015_ipyleaflet.html')
    files.download('displacement.tif')